### Crawl


#### Playlist

Genres to crawl : 
- Pop
- Instrumental
- Jazz
- Electronic
- Rock
- Classical
- Folk
- Country
- Vietnamese pop

#### Crawl all

In [1]:
import os 
import pandas as pd

DATASET_PATH = 'data/'
AUDIO_PATH = os.path.join(DATASET_PATH + 'audio') 

In [16]:
df_spotify_original = pd.read_csv(DATASET_PATH + "tracks_metadata.csv")

In [11]:
from scraper import Request, Scraper

request = Request().request()
scraper = Scraper(session=request)

In [9]:
# urls_dict = {"pop" : ["https://open.spotify.com/playlist/37i9dQZF1DXcBWIGoYBM5M",
#                       "https://open.spotify.com/playlist/37i9dQZF1DXcRXFNfZr7Tp"], 
#              "instrumental" : ["https://open.spotify.com/playlist/37i9dQZF1DX9j444F9NCBa"],
#              "rock" : ["https://open.spotify.com/playlist/37i9dQZF1DWZryfp6NSvtz",
#                        "https://open.spotify.com/playlist/37i9dQZF1DX5a39zUmS7Hn"],
#              "country" : ["https://open.spotify.com/playlist/37i9dQZF1DX1lVhptIYRda",
#                           "https://open.spotify.com/playlist/37i9dQZF1DX8S0uQvJ4gaa"],
#              "electronic" : ["https://open.spotify.com/playlist/37i9dQZF1DX1zRNi3kxIg2",
#                              "https://open.spotify.com/playlist/37i9dQZF1DX7D8GQsPKGvy"],
#              "hiphop" : ["https://open.spotify.com/playlist/37i9dQZF1DX2M1RktxUUHG",
#                          "https://open.spotify.com/playlist/37i9dQZF1DX58gKmCfKS2T"],
#              "jazz" : ["https://open.spotify.com/playlist/37i9dQZF1DXbITWG1ZJKYt"],
#              "classical" : ["https://open.spotify.com/playlist/37i9dQZF1DWV0gynK7G6pD",
#                             "https://open.spotify.com/playlist/37i9dQZF1DWWEJlAGA9gs0"]}

urls_dict = {"pop" : ["https://open.spotify.com/playlist/37i9dQZF1DXcBWIGoYBM5M",
                        "https://open.spotify.com/playlist/37i9dQZF1DXcRXFNfZr7Tp"]}

In [5]:

df_whole = pd.DataFrame() 

for item, values in urls_dict.items() : 
    print(item)
    tracks_df = scraper.get_playlist_tracks_info(values, genre=item)
    tracks_df = scraper.crawl_and_append_track_info(tracks_df)
    tracks_df = tracks_df.dropna(subset=['preview_mp3'])
    # check duplicates 
    tracks_df = tracks_df[~tracks_df['track_id'].isin(df_spotify_original['track_id'])]
    if 'track_id' in df_whole.columns:
        df_whole = pd.concat([df_whole, tracks_df[~tracks_df['track_id'].isin(df_whole['track_id'])]], ignore_index=True)
    else:
        df_whole = pd.concat([df_whole, tracks_df], ignore_index=True)


instrumental
<script id="__NEXT_DATA__" type="application/json">{"props":{"pageProps":{"_sentryTraceData":"c435f3a1cd0d4f398771ef481fdf336d-990585b0adc6ed29-0","_sentryBaggage":"sentry-environment=production,sentry-release=8c441722-5878-41e4-adc2-c779d2d096f7,sentry-public_key=4cc707ab12ea4779b417479c0550a5cb,sentry-trace_id=c435f3a1cd0d4f398771ef481fdf336d,sentry-sample_rate=0,sentry-transaction=%2Ftrack%2F%5Bid%5D,sentry-sampled=false","state":{"data":{"entity":{"type":"track","name":"Dancing on my own","uri":"spotify:track:122XrAD5sOasFPY1eKUfCt","id":"122XrAD5sOasFPY1eKUfCt","title":"Dancing on my own","artists":[{"name":"Zach Flash","uri":"spotify:artist:245BfbwD5kOa5wFTd0Bl5w"}],"coverArt":{"extractedColors":{"colorDark":{"hex":"#004838"},"colorLight":{"hex":"#008769"}},"sources":[{"url":"https://i.scdn.co/image/ab67616d00001e024930133959f2f53a9461e1f8","width":300,"height":300},{"url":"https://i.scdn.co/image/ab67616d000048514930133959f2f53a9461e1f8","width":64,"height":64},{"ur

In [21]:
df_whole.to_csv(DATASET_PATH + "tracks_metadata_23_03.csv", index=False, mode='a', header=False)

#### Download mp3 audio

In [23]:
scraper.download_preview_mp3(df_whole, path=AUDIO_PATH+"/23_03_2024")

#### Using Spotify API 

In [24]:
from dotenv import load_dotenv
import os 
import base64
import requests
import json
import webbrowser
from urllib.parse import urlencode

load_dotenv() 

client_id = os.getenv("CLIENT_ID") 
client_secret = os.getenv("CLIENT_SECRET") 
redirect_uri = os.getenv("REDIRECT_URI")  

def get_authorization_code() : 
    auth_headers = {
        "client_id" : client_id,
        "response_type" : "code",
        "redirect_uri" : "http://localhost:3000",
        "scope" : "user-library-read"
    }
    
    webbrowser.open("https://accounts.spotify.com/authorize?" + urlencode(auth_headers))




In [25]:
get_authorization_code() 

In [26]:
# trên redirect url sẽ có dạng http://localhost:3000/?code=....
# copy giá trị của code paste vào đây
code = "AQCr2VBNM1zpbBLusFgDkYgNujEm5zJIU8qesxhSV9tBYmvbQUM_MWAJGb9s_kzAFCLP820GMJ7bRwDTYFUMnYadkrat_drwYppYaR8ASoKIw-4vcfreh1I0bvxo5N7NY3r4L_dTzG6YexwnYWCdbXUh-jdFX5G89nquH2IL1i_PEgVjTKYGjYRhEDY"

In [27]:
def get_token() : 
    auth_string = client_id + ":" + client_secret
    auth_bytes = auth_string.encode("utf-8") 
    auth_base64 = str(base64.b64encode(auth_bytes), "utf-8") 
    
    url = "https://accounts.spotify.com/api/token" 
    headers = {
        "Authorization" : "Basic " + auth_base64,
        "content-type" : "application/x-www-form-urlencoded"  
    }
    token_data = {
        "grant_type" :"authorization_code",
        "code" : code,
        "redirect_uri" : "http://localhost:3000"
    } 
    result = requests.post(url, headers=headers, data=token_data) 
    json_result = json.loads(result.content) 
    # print(json_result)
    token = json_result["access_token"] 
    return token 

token = get_token() 
print(token)

BQAh9EeeuRJs35qf-ZVcPZ5YISdvlpMz9BgR60koFbMqGhs5IV8RT_ASKWCVjfv1DBiyetGCQrHLc8A2Y7ZaBM9mmz8S6bcJZ6CvEQ4U8-OZqdrE54S7krC_85MRP9UV0zvsNIHRKCSOvM2y9S9eKd1sVJczoHvLQivvSfqZwzOBN_7BiU_Z6NuoMSYk1LWmqvKyj116pHYzRKc


In [28]:
def get_audio_features(track_ids) : 
    api_url = "https://api.spotify.com/v1/audio-features"
    user_headers = {
        "Authorization": "Bearer " + token,
        "Content-Type": "application/json"
    } 
    params = {"ids": ",".join(track_ids)}
    response = requests.get(api_url, headers=user_headers, params=params)
    
    if response.status_code == 200:
        return response.json()["audio_features"]
    else:
        print(f"Failed to get audio features. Status code: {response.status_code}")
        return None
      

In [29]:
def get_audio_features_dataframe(df : pd.DataFrame) : 
    if token : 
        chunk_size = 100 
        total_rows = len(df) 
        
        for i in range(0, total_rows, chunk_size) : 
            print("i=",i)
            current_chunk_size = min(chunk_size, total_rows-i) 
            
            if total_rows < chunk_size : 
                track_ids = df.loc[i:i+current_chunk_size, "track_id"].tolist() 
            else : 
                track_ids = df.loc[i:i+current_chunk_size-1, "track_id"].tolist() 
            
            audio_features = get_audio_features(track_ids) 
            
            # print(audio_features)
            if audio_features : 
                audio_features_df = pd.DataFrame(audio_features) 
                audio_features_df = audio_features_df.drop(columns=["analysis_url", "duration_ms", "id", "track_href", "type", "uri"], axis=1) 
                if total_rows < chunk_size : 
                    df.loc[i:i + current_chunk_size, audio_features_df.columns] = audio_features_df.values
                else : 
                    df.loc[i:i + current_chunk_size - 1, audio_features_df.columns] = audio_features_df.values
        
    return df
            


In [30]:
new_df_with_audio_features = get_audio_features_dataframe(df_whole)
new_df_with_audio_features

i= 0
i= 100
i= 200
i= 300
i= 400
i= 500
i= 600
i= 700
i= 800
i= 900
i= 1000
i= 1100
i= 1200
i= 1300
i= 1400


track_title  \
0                                      Beautiful Things   
1                                              obsessed   
2              we can't be friends (wait for your love)   
3                                          Lose Control   
4                                        TEXAS HOLD 'EM   
...                                                 ...   
1475                      Young Birches, Op. 128, No. 2   
1476  Violin Concerto In D Major, Op. 35: III. Final...   
1477  Tahiti Trot, Op. 16 (After V. Youmans's "Tea f...   
1478                                        The Promise   
1479                       Carmina Burana: I. O Fortuna   

                                              track_url  \
0     https://open.spotify.com/track/6tNQ70jh4OwmPGp...   
1     https://open.spotify.com/track/6tNgRQ0K2NYZ0Rb...   
2     https://open.spotify.com/track/46kspZSY3aKmwQe...   
3     https://open.spotify.com/track/6usohdchdzW9oML...   
4     https://open.spotify.com/track/0Z7nGFVCLfixWct...   
...                                                 ...   
1475  https://open.spotify.com/track/4VVEfBXep7FdOt5...   
1476  https://open.spotify.com/track/7hOLwSaTSkrqxSM...   
1477  https://open.spotify.com/track/1uARLLfeQPlBf1j...   
1478  https://open.spotify.com/track/53ann6bENp7BF8u...   
1479  https://open.spotify.com/track/0qFZYO72iBOhW7X...   

                                            track_album      genre  \
0                                      Beautiful Things        pop   
1                                        GUTS (spilled)        pop   
2                                      eternal sunshine        pop   
3                                          Lose Control        pop   
4                                        TEXAS HOLD 'EM        pop   
...                                                 ...        ...   
1475  Beach: Variations on Balkan Themes Op. 60, Mar...  classical   
1476           Tchaikovsky / Korngold: Violin Concertos  classical   
1477                     Shostakovich: Orchestral Works  classical   
1478           The Piano: Music From The Motion Picture  classical   
1479                               Orff: Carmina Burana  classical   

                    track_id  \
0     6tNQ70jh4OwmPGpYy6R2o9   
1     6tNgRQ0K2NYZ0Rb9l9DzL8   
2     46kspZSY3aKmwQe7O77fCC   
3     6usohdchdzW9oML7VC4Uhk   
4     0Z7nGFVCLfixWctgePsRk9   
...                      ...   
1475  4VVEfBXep7FdOt524jkfLF   
1476  7hOLwSaTSkrqxSMzj4bXI1   
1477  1uARLLfeQPlBf1jSN4P0yK   
1478  53ann6bENp7BF8uklrzQAp   
1479  0qFZYO72iBOhW7X6KbL44Q   

                                            preview_mp3 duration  \
0     https://p.scdn.co/mp3-preview/e213f23e6fe59382...      3:0   
1     https://p.scdn.co/mp3-preview/0dee7e994f64604e...     2:50   
2     https://p.scdn.co/mp3-preview/aa7d619d38c678b2...     3:48   
3     https://p.scdn.co/mp3-preview/51e51cc257e41868...     3:30   
4     https://p.scdn.co/mp3-preview/049e763cb1a9fe9e...     3:55   
...                                                 ...      ...   
1475  https://p.scdn.co/mp3-preview/4284c8051d3092d9...     2:39   
1476  https://p.scdn.co/mp3-preview/0d830235e2e00eec...      7:4   
1477  https://p.scdn.co/mp3-preview/db8939ca3d276c1b...      4:9   
1478  https://p.scdn.co/mp3-preview/6c079bb5063259bb...     4:16   
1479  https://p.scdn.co/mp3-preview/12020ff92759a008...     2:47   

                  artist_name  \
0                Benson Boone   
1              Olivia Rodrigo   
2               Ariana Grande   
3                 Teddy Swims   
4                     Beyoncé   
...                       ...   
1475                Amy Beach   
1476  Erich Wolfgang Korngold   
1477      Dmitri Shostakovich   
1478            Michael Nyman   
1479                Carl Orff   

                                             artist_url          release_date  \
0     https://open.spotify.com/artist/22wbnEMDvgVIAG...  2024-01-18T00:00:00Z   
1     https://open.spoti

In [31]:
new_df_with_audio_features.to_csv(DATASET_PATH + "tracks_metadata_23_03.csv", index=False)

In [43]:
# run this cell when you accidentally write df_whole to tracks_metadata.csv

# import pandas as pd

# # Read the original tracks_metadata.csv file
# original_df = pd.read_csv(DATASET_PATH + "tracks_metadata.csv")

# # Remove the rows in original_df that have the same track_id as those in new_df_with_audio_features
# original_df_1 = original_df[~original_df['track_id'].isin(new_df_with_audio_features['track_id'])]

# # Append the rows from new_df_with_audio_features to original_df
# merged_df = pd.concat([original_df_1, new_df_with_audio_features], ignore_index=True)

# # Write the merged dataframe to the csv file
# merged_df.to_csv(DATASET_PATH + "tracks_metadata.csv", index=False)

In [80]:
# append to csv
new_df_with_audio_features.to_csv(DATASET_PATH+"tracks_metadata.csv",mode='a',header=False, index=False)